## Part 1: data processing neighborhood polygons (LA Times via maps.latimes.com)

Before looking at food we need to better understand the geography of this region. Specifically, we need an effective method of subdividing LA, that is hopefully somewhat related to the culinary make-up of various neighborhoods. One approach is to use official subdivisions, like zipcodes or county lines. This dataset could work well, but the boundaries may not be related to the actual city neighborhoods. When one neighborhood expands and others converge, zipcodes will not follow, for example. 

I came across a more representative dataset from the LA Times that was drawn with input from hundreds of residents of the city. Let's download their JSON file from <a href="https://s3-us-west-2.amazonaws.com/mappingla.com/downloads/neighborhoods/la_county.json">here</a> and check out the boundaries using GeoPandas and folium's choropleth map. Look <a href="http://maps.latimes.com/neighborhoods/">here</a> for an outline of the LA Times project.

In [1]:
#First grab the modules I'll need in this data processing...
import pandas as pd
import geopandas as gpd
import folium
from shapely.geometry import Point
import wget
import haversine

First I'll take a quick look at LA using Folium to get oriented.

In [2]:
la_coords = [34.0522, -118.2437]#coordinates for LA 
# create a plain map of LA with polygon coordinates from la_county.json
la_map = folium.Map(location=la_coords, zoom_start=9)
la_map

Next, I'll download the data in JSON format with wget and plot it with folium.

In [3]:
url = 'https://s3-us-west-2.amazonaws.com/mappingla.com/downloads/neighborhoods/la_county.json'
wget.download(url, 'raw/la_county.json')

100% [..........................................................................] 3972932 / 3972932

'raw/la_county (1).json'

In [4]:
la_coords = [34.0522, -118.2437]#coordinates for LA 
# create a plain map of LA with polygon coordinates from la_county.json
la_map = folium.Map(location=la_coords, zoom_start=9, tiles='cartodbpositron')
la_map.choropleth(
   geo_data=r'raw/la_county.json',
   fill_opacity=0.1, 
   line_opacity=1.0,
   fill_color='green')
#la_map.save('la_times.html')#save figure so I can generate plots later
la_map

In order to find restaurant data in the next section we'll need the center of each neighborhood polygon. Let's use GeoPandas to read the JSON file and find the center (defined as center-of-mass) for each neighborhood:

In [5]:
la_geo = r'raw/la_county.json'
polys = gpd.read_file(la_geo)
polys['centroids'] = polys['geometry'].centroid
polys = polys.set_geometry('centroids')
polys.set_index('name', inplace=True)
polys.drop('slug',axis=1, inplace=True)
polys.head(5) #let's check out the first 5 rows:

geometry  \
name                                                                 
Acton            (POLYGON ((-118.202617 34.53899, -118.198235 3...   
Adams-Normandie  (POLYGON ((-118.309008 34.037411, -118.305708 ...   
Agoura Hills     (POLYGON ((-118.761925 34.168203, -118.761854 ...   
Agua Dulce       (POLYGON ((-118.254677 34.558304, -118.254876 ...   
Alhambra         (POLYGON ((-118.121747 34.10504, -118.121723 3...   

                                                    centroids  
name                                                           
Acton            POINT (-118.1858079060971 34.49551742275847)  
Adams-Normandie   POINT (-118.300300561171 34.03139821255268)  
Agoura Hills     POINT (-118.7609336216224 34.15073618354409)  
Agua Dulce       POINT (-118.3133681618562 34.50891540114063)  
Alhambra         POINT (-118.1354927559934 34.08395839026004)

Computing distance from latitude and longitude values is a little tricky, because the Earth has a curved surface and longitude spacings are not conserved. One approach is to use the <a href="https://en.wikipedia.org/wiki/Haversine_formula">Haversine formula</a> compute distance. It assumes the Earth is a sphere, and finds the great circle distance between points. Let's compute the distance from the center of Downtown to the center of each neighborhood: 

Then, compute the distance from the center of Downtown to the center of each neighborhood: 

In [6]:
distances_list = haversine.haver(polys['centroids'].x,polys['centroids'].y,polys.loc['Downtown']['centroids'].x,polys.loc['Downtown']['centroids'].y)
polys['distance_to_DTLA'] = distances_list
polys.head(5)#check out first 5 rows of the table

geometry  \
name                                                                 
Acton            (POLYGON ((-118.202617 34.53899, -118.198235 3...   
Adams-Normandie  (POLYGON ((-118.309008 34.037411, -118.305708 ...   
Agoura Hills     (POLYGON ((-118.761925 34.168203, -118.761854 ...   
Agua Dulce       (POLYGON ((-118.254677 34.558304, -118.254876 ...   
Alhambra         (POLYGON ((-118.121747 34.10504, -118.121723 3...   

                                                    centroids  \
name                                                            
Acton            POINT (-118.1858079060971 34.49551742275847)   
Adams-Normandie   POINT (-118.300300561171 34.03139821255268)   
Agoura Hills     POINT (-118.7609336216224 34.15073618354409)   
Agua Dulce       POINT (-118.3133681618562 34.50891540114063)   
Alhambra         POINT (-118.1354927559934 34.08395839026004)   

                 distance_to_DTLA  
name                               
Acton                   51.059704  
Adams-Normandie          5.083596  
Agoura Hills            49.024654  
Agua Dulce              52.616413  
Alhambra                11.332059

Now, we'll get rid of any neighborhoods further than 30 km from the center of Downtown:

In [7]:
polys = polys[polys['distance_to_DTLA'] < 30]
polys.reset_index(inplace=True)

Let's see the resulting neighborhood centroids. The map is interactive -- click on it to see the name of each neighborhood!

In [8]:
la_coords = [34.0522, -118.2437]#coordinates for LA 
map_clusters = folium.Map(location=la_coords,zoom_start=10, tiles='cartodbpositron')
for latlon, name in zip(polys['centroids'], polys['name']):
    label = folium.Popup(str(name))
    folium.CircleMarker(
        [latlon.y,latlon.x],
        radius=5,
        popup=label,
        fill=True,
        fill_opacity=0.7).add_to(map_clusters)
map_clusters

And finally we'll find the distance from the center of each neighborhood to the furthest point in the polygon. We'll need this when we access restaurant data with the Foursquare API.

In [9]:
#iterate over dataframe and find largest distance from center point to outer points to capture full neighborhood
try: polys['geometry'] = polys['geometry'].apply(lambda x: x[0])
except:pass
r_list = []
for index, row in polys[['geometry','centroids']].iterrows():
    lat_list = []
    long_list = []
    a = row['geometry']
    lon2 = row['centroids'].x
    lat2 = row['centroids'].y
    for v in a.exterior.coords:
        long_list.append(v[0])
        lat_list.append(v[1])
    haver_list = haversine.haver(long_list, lat_list, lon2, lat2)
    haver_list.sort(reverse=True)
    r_list.append(haver_list[0])   
polys['r_list']=r_list
polys.head(5)

name                                           geometry  \
0  Adams-Normandie  POLYGON ((-118.309008 34.037411, -118.305708 3...   
1         Alhambra  POLYGON ((-118.121747 34.10504, -118.121723 34...   
2     Alondra Park  POLYGON ((-118.326513 33.897572, -118.32651 33...   
3         Altadena  POLYGON ((-118.151354 34.215508, -118.149304 3...   
4          Arcadia  POLYGON ((-118.017052 34.177182, -118.018186 3...   

                                      centroids  distance_to_DTLA    r_list  
0   POINT (-118.300300561171 34.03139821255268)          5.083596  1.048783  
1  POINT (-118.1354927559934 34.08395839026004)         11.332059  3.621182  
2  POINT (-118.3349530824924 33.88851871541979)         18.641472  1.683572  
3  POINT (-118.1355556519902 34.19346062411022)         19.952616  4.868231  
4   POINT (-118.037234702483 34.13408461516024)         21.932021  6.326122

Finally output to shape files. Unfortunately geopandas only allows one geometry containing column for each file so we have to put it into two files:

In [10]:
polys[['name','centroids', 'r_list']].to_file('processed/la_times_centroids.shp')
polys.set_geometry('geometry')[['name','geometry']].to_file('processed/la_times_polygons.shp')

C:\Users\ianfi\Anaconda3\lib\site-packages\geopandas\io\file.py:108: FionaDeprecationWarning: Use fiona.Env() instead.
  with fiona.drivers():
